## LightGBM-Optunaのサンプルコード

In [1]:
%load_ext lab_black

In [2]:
# ライブラリーのインポート
import os

import pandas as pd
import numpy as np

import seaborn as sns
import matplotlib.pyplot as plt

%matplotlib inline

# ボストンの住宅価格データ
from sklearn.datasets import load_boston

# 前処理
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

# LightGBM
import optuna.integration.lightgbm as lgb

# 評価指標
from sklearn.metrics import r2_score
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error

In [3]:
# データセットの読込み
boston = load_boston()

# 説明変数の格納
df = pd.DataFrame(boston.data, columns=boston.feature_names)
# 目的変数の追加
df["MEDV"] = boston.target

# データの中身を確認
df.head()

CRIM    ZN  INDUS  CHAS    NOX     RM   AGE     DIS  RAD    TAX  \
0  0.00632  18.0   2.31   0.0  0.538  6.575  65.2  4.0900  1.0  296.0   
1  0.02731   0.0   7.07   0.0  0.469  6.421  78.9  4.9671  2.0  242.0   
2  0.02729   0.0   7.07   0.0  0.469  7.185  61.1  4.9671  2.0  242.0   
3  0.03237   0.0   2.18   0.0  0.458  6.998  45.8  6.0622  3.0  222.0   
4  0.06905   0.0   2.18   0.0  0.458  7.147  54.2  6.0622  3.0  222.0   

   PTRATIO       B  LSTAT  MEDV  
0     15.3  396.90   4.98  24.0  
1     17.8  396.90   9.14  21.6  
2     17.8  392.83   4.03  34.7  
3     18.7  394.63   2.94  33.4  
4     18.7  396.90   5.33  36.2

#### 前処理

In [4]:
# ランダムシード値
RANDOM_STATE = 10

# 学習データと評価データの割合
TEST_SIZE = 0.2

# 学習データと評価データを作成
x_train, x_test, y_train, y_test = train_test_split(
    df.iloc[:, 0 : df.shape[1] - 1],
    df.iloc[:, df.shape[1] - 1],
    test_size=TEST_SIZE,
    random_state=RANDOM_STATE,
)

# trainのデータセットの2割をモデル学習時のバリデーションデータとして利用する
x_train, x_valid, y_train, y_valid = train_test_split(
    x_train, y_train, test_size=TEST_SIZE, random_state=RANDOM_STATE
)

# LightGBMを利用するのに必要なフォーマットに変換
lgb_train = lgb.Dataset(x_train, y_train)
lgb_eval = lgb.Dataset(x_valid, y_valid, reference=lgb_train)

In [5]:
# ベストなパラメータ、途中経過を保存する
params = {
    "objective": "mean_squared_error",
    "metric": "rmse",
    "verbosity": 10,
    "boosting_type": "gbdt",
    "random_seed": 0,
}

best_params, history = {}, []

# LightGBM学習
gbm = lgb.train(
    params,
    lgb_train,
    num_boost_round=1000,
    valid_sets=[lgb_train, lgb_eval],
    early_stopping_rounds=100,
    verbose_eval=50,
)

[I 2021-07-07 12:36:48,673] A new study created in memory with name: no-name-075c5ae8-b8bd-418d-af63-61b024439331
feature_fraction, val_score: inf:   0%|          | 0/7 [00:00<?, ?it/s]

[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.832817
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.128126
[LightGBM] [Debug] init for col-wise cost 0.002115 seconds, init for row-wise cost 0.001223 seconds
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001273 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 809
[LightGBM] [Info] Number of data points in the train set: 323, number of used features: 13
[LightGBM] [Info] Start training from score 21.968731
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 13 and max_depth = 5
Training until validation scores don't improve for 100 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 13 and max_depth = 6
[LightGBM] [Warning] No further splits with positi

feature_fraction, val_score: 3.025665:  14%|#4        | 1/7 [00:02<00:13,  2.20s/it]

[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.832817
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.128126
[LightGBM] [Debug] init for col-wise cost 0.001625 seconds, init for row-wise cost 0.001414 seconds
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001469 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 809
[LightGBM] [Info] Number of data points in the train set: 323, number of used features: 13
[LightGBM] [Info] Start training from score 21.968731
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 12 and max_depth = 6
Training until validation scores don't improve for 100 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 13 and max_depth = 8
[LightGBM] [Warning] No further splits with positi

feature_fraction, val_score: 3.025665:  29%|##8       | 2/7 [00:02<00:06,  1.28s/it]

...

[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.832817
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.128126
[LightGBM] [Debug] init for col-wise cost 0.001989 seconds, init for row-wise cost 0.001676 seconds
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.008687 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Debug] Using Dense Multi-Val Bin
[LightGBM] [Info] Total Bins 809
[LightGBM] [Info] Number of data points in the train set: 323, number of used features: 13
[LightGBM] [Info] Start training from score 21.968731
[LightGBM] [Debug] Re-bagging, using 304 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 2 and max_depth = 1
Training until validation scores don't improve for 100 rounds
[LightGBM] [Debug] Re-bagging, 

min_data_in_leaf, val_score: 2.702409:  80%|########  | 4/5 [00:22<00:04,  4.28s/it]

[LightGBM] [Debug] Re-bagging, using 306 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 2 and max_depth = 1
[LightGBM] [Debug] Re-bagging, using 308 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 2 and max_depth = 1
[LightGBM] [Debug] Re-bagging, using 313 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 2 and max_depth = 1
[LightGBM] [Debug] Re-bagging, using 311 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 3 and max_depth = 2
[LightGBM] [Debug] Re-bagging, using 313 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 3 and max_depth = 2
[LightGBM]

min_data_in_leaf, val_score: 2.702409: 100%|##########| 5/5 [00:23<00:00,  4.72s/it]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 10 and max_depth = 8
[LightGBM] [Debug] Re-bagging, using 313 data to train
[LightGBM] [Debug] Trained a tree with leaves = 11 and max_depth = 6
[LightGBM] [Debug] Re-bagging, using 312 data to train
[LightGBM] [Debug] Trained a tree with leaves = 11 and max_depth = 5
[LightGBM] [Debug] Re-bagging, using 311 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 8 and max_depth = 5
[LightGBM] [Debug] Re-bagging, using 306 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 9 and max_depth = 5
[LightGBM] [Debug] Re-bagging, using 310 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 9 and max_depth = 6
[LightGBM] [De

In [6]:
best_params = gbm.params
best_params

{'objective': 'mean_squared_error',
 'metric': 'rmse',
 'verbosity': 10,
 'boosting_type': 'gbdt',
 'random_seed': 0,
 'feature_pre_filter': False,
 'lambda_l1': 0.0,
 'lambda_l2': 0.0,
 'num_leaves': 11,
 'feature_fraction': 0.7,
 'bagging_fraction': 0.9592807442353714,
 'bagging_freq': 1,
 'min_child_samples': 5,
 'num_iterations': 1000,
 'early_stopping_round': 100}

In [7]:
# LightGBM推論
y_pred = gbm.predict(x_test, num_iteration=gbm.best_iteration)

In [8]:
# 評価
def calculate_scores(true, pred):
    """全ての評価指標を計算する

    Parameters
    ----------
    true (np.array)       : 実測値
    pred (np.array)       : 予測値

    Returns
    -------
    scores (pd.DataFrame) : 各評価指標を纏めた結果

    """
    scores = {}
    scores = pd.DataFrame(
        {
            "R2": r2_score(true, pred),
            "MAE": mean_absolute_error(true, pred),
            "MSE": mean_squared_error(true, pred),
            "RMSE": np.sqrt(mean_squared_error(true, pred)),
        },
        index=["scores"],
    )
    return scores

In [9]:
scores = calculate_scores(y_test, y_pred)
print(scores)

              R2       MAE        MSE     RMSE
scores  0.856609  2.620807  14.995947  3.87246
